In [1]:
using FundamentalsNumericalComputation
FNC.init_format()

┌ Info: verify download of index files...
└ @ MatrixDepot /Users/driscoll/.julia/packages/MatrixDepot/GEDc3/src/MatrixDepot.jl:139
┌ Info: reading database
└ @ MatrixDepot /Users/driscoll/.julia/packages/MatrixDepot/GEDc3/src/download.jl:23
┌ Info: adding metadata...
└ @ MatrixDepot /Users/driscoll/.julia/packages/MatrixDepot/GEDc3/src/download.jl:67
┌ Info: adding svd data...
└ @ MatrixDepot /Users/driscoll/.julia/packages/MatrixDepot/GEDc3/src/download.jl:69
┌ Info: writing database
└ @ MatrixDepot /Users/driscoll/.julia/packages/MatrixDepot/GEDc3/src/download.jl:74
┌ Info: used remote sites are sparse.tamu.edu with MAT index and math.nist.gov with HTML index
└ @ MatrixDepot /Users/driscoll/.julia/packages/MatrixDepot/GEDc3/src/MatrixDepot.jl:141


(section-intro-stability)=
# Stability

```{index} ! stability
```

If we solve a problem using a computer algorithm and see a large error in the result, we might suspect poor conditioning in the original mathematical problem. But algorithms can also be sources of errors. When error in the result of an algorithm exceeds what conditioning can explain, we call the algorithm **unstable**.

## Case study

In {numref}`Example %s <example-quad-root-cond>` we showed that finding the roots of a quadratic polynomial $ax^2 + b x+c$ is poorly conditioned if and only if the roots are close to each other relative to their size. Hence for the polynomial

```{math}
:label: quadunstable
p(x) = (x-10^6)(x-10^{-6}) = x^2 - (10^6+10^{-6})x + 1,
```

finding roots is a well-conditioned problem. An obvious algorithm for finding those roots is to directly apply the familiar quadratic formula,

```{math}
:label: quadform
x_1 = \frac{-b + \sqrt{b^2-4ac}}{2a}, \qquad
x_2 = \frac{-b - \sqrt{b^2-4ac}}{2a}.
```

(demo-stability-quadbad)=
```{proof:demo}
```

```{raw} html
<div class='demo'>
```

```{raw} latex
%%start demo%%
```

```{index} ! Julia; scientific notation
```

::::{panels}
:column: col-7 left-side
:card: border-0 shadow-none
```{raw} latex
\begin{minipage}[t]{0.5\textwidth}
```
We apply the quadratic formula to find the roots of a quadratic via {eq}`quadunstable`. 

```{raw} latex
\end{minipage}\hfill
```
---
:column: col-5 right-side
:card: shadow-none comment 
```{raw} latex
\begin{minipage}[t]{0.4\textwidth}\begin{mdframed}[default]\small
```
A number in scientific notation is entered as `1.23e4` rather than as `1.23*10^{4}`.
```{raw} latex
\end{mdframed}\end{minipage}
```
::::

In [2]:
a = 1;  b = -(1e6+1e-6);  c = 1;
@show x₁ = (-b + sqrt(b^2-4a*c)) / 2a;
@show x₂ = (-b - sqrt(b^2-4a*c)) / 2a;

x₁ = (-b + sqrt(b ^ 2 - (4a) * c)) / (2a) = 1.0e6
x₂ = (-b - sqrt(b ^ 2 - (4a) * c)) / (2a) = 1.00000761449337e-6


The first value is correct to all stored digits, but the second has fewer than six accurate digits:

In [3]:
error = abs(1e-6-x₂)/1e-6 
@show accurate_digits = -log10(error);

accurate_digits = -(log10(error)) = 5.118358987126217


 The instability is easily explained. Since $a=c=1$, we treat them as exact numbers. First, we compute the condition numbers with respect to $b$ for each elementary step in finding the "good" root:

| Calculation | Result | $\kappa$ |
|:------------|:-------|:---------|
|$u_1 = b^2$  | $1.000000000002000\times 10^{12}$ |  2 |
|$u_2 = u_1 - 4$ | $9.999999999980000\times 10^{11}$  | $\approx 1.00$ |
|$u_3 = \sqrt{u_2}$ | $999999.9999990000$ | 1/2 |
|$u_4 = u_3 - b$ | $2000000$ | $\approx 0.500$ |
|$u_5 = u_4/2$ | $1000000$  | 1 |

Using {eq}`condition-chain`, the chain rule for condition numbers, the conditioning of the entire chain is the product of the individual steps, so there is essentially no growth of relative error here. However, if we use the quadratic formula for the "bad" root, the next-to-last step becomes $u_4=(-u_3) - b$, and now  $\kappa=|u_3|/|u_4|\approx 5\times 10^{11}$. So we can expect to lose 11 digits of accuracy, which is what we observed. The key issue is the subtractive cancellation in this one step.

```{raw} html
</div>
```

```{raw} latex
%%end demo%%
```

```{index} subtractive cancellation
```

{numref}`Demo %s <demo-stability-quadbad>` suggests that the venerable quadratic formula is an *unstable* means of computing roots in finite precision. The roots themselves were not sensitive to the data or arithmetic—it's the specific computational path we chose that caused the huge growth in errors. 

We can confirm this conclusion by finding a different path that avoids subtractive cancellation. A little algebra using {eq}`quadform` confirms the additional formula $x_1x_2=c/a$.  So given one root $r$, we compute the other root using $c/ar$, which has only multiplication and division and therefore creates no numerical trouble.

(demo-stability-quadgood)=
```{proof:demo}
```

```{raw} html
<div class='demo'>
```

```{raw} latex
%%start demo%%
```

We repeat the rootfinding experiment of {numref}`Demo %s <demo-stability-quadbad>` with an alternative algorithm.

In [4]:
a = 1;  b = -(1e6+1e-6);  c = 1;

First, we find the "good" root using the quadratic formula.

In [5]:
@show x₁ = (-b + sqrt(b^2-4a*c)) / 2a;

x₁ = (-b + sqrt(b ^ 2 - (4a) * c)) / (2a) = 1.0e6


Then we use the identity $x_1x_2=\frac{c}{a}$ to compute the smaller root:

In [6]:
@show x₂ = c / (a*x₁);

x₂ = c / (a * x₁) = 1.0e-6


As you see in this output, Julia often suppresses trailing zeros in a decimal expansion. To be sure we have an accurate result, we compute its relative error.

In [7]:
abs(x₂-1e-6) / 1e-6

0.0

```{raw} html
</div>
```

```{raw} latex
%%end demo%%
```

The algorithms in {numref}`Demo {number} <demo-stability-quadbad>` and {numref}`Demo {number} <demo-stability-quadgood>` are equivalent when using real numbers and exact arithmetic. When results are perturbed by machine representation at each step, though, the effects may depend dramatically on the specific sequence of operations, thanks to the chain rule {eq}`condition-chain`.

::::{proof:observation}
The sensitivity of a problem $f(x)$ is governed only by $\kappa_f$, but the sensitivity of an algorithm depends on the condition numbers of all of its individual steps. 
::::

This situation may seem hopelessly complicated. But the elementary operations we take for granted, such as those in {numref}`table-condition-functions`, are well-conditioned in most circumstances. Exceptions usually occur when $|f(x)|$ is much smaller than $|x|$, although not every such case signifies trouble. The most common culprit is simple subtractive cancellation.

A practical characterization of instability is that results are much less accurate than the conditioning of the problem can explain. Typically one should apply an algorithm to test problems whose answers are well-known, or for which other programs are known to work well, in order to spot possible instabilities. In the rest of this book we will see some specific ways in which instability is manifested for different types of problems.

## Backward error

In the presence of poor conditioning for a problem $f(x)$, even just the act of rounding the data to floating point may introduce a large change in the result. It's not realistic, then, to expect any algorithm $\tilde{f}$ to have a small error in the sense $\tilde{f}(x)\approx f(x)$. There is another way to characterize the error, though, that can be a useful alternative measurement. Instead of asking, "Did you get nearly the right answer?", we ask, "Did you answer nearly the right question?"

```{index} ! backward error
```

(definition-stability-backward)=
:::{proof:definition} Backward error
Let $\tilde{f}$ be an algorithm for the problem $f$. Let $y=f(x)$ be an exact result and $\tilde{y}=\tilde{f}(x)$ be its approximation by the algorithm. If there is a value $\tilde{x}$ such that $f(\tilde{x}) = \tilde{y}$, then the relative **backward error** in $\tilde{y}$ is 

```{math}
:label: backwarderror
\frac{ |\tilde{x}-x| } { |x| }. 
```

The absolute backward error is $|\tilde{x}-x|$.
:::

Backward error measures the change to the original data that reproduces the result that was found by the algorithm. The situation is illustrated in {numref}`fig-backwarderror`. 

```{figure} figures/backwarderror.svg
:name: fig-backwarderror
Backward error is the difference between the original data and the data that exactly produces the computed value.
```

(demo-stability-roots)=
```{proof:demo}
```

```{raw} html
<div class='demo'>
```

```{raw} latex
%%start demo%%
```

::::{panels}
:column: col-7 left-side
:card: border-0 shadow-none
```{raw} latex
\begin{minipage}[t]{0.5\textwidth}
```
For this example we will use the `Polynomials` package, which is installed by the `FNC` package.  

```{raw} latex
\end{minipage}\hfill
```
---
:column: col-5 right-side
:card: shadow-none comment 
```{raw} latex
\begin{minipage}[t]{0.4\textwidth}\begin{mdframed}[default]\small
```
In the rest of the book, we do not show the `using` statement needed to load the book's package, but you will need to enter it if you want to run the codes yourself.
```{raw} latex
\end{mdframed}\end{minipage}
```
::::

In [8]:
using FundamentalsNumericalComputation

Our first step is to construct a polynomial with six known roots.

In [9]:
r = [-2.0,-1,1,1,3,6]
p = fromroots(r)

Polynomial(36.0 - 36.0*x - 43.0*x^2 + 44.0*x^3 + 6.0*x^4 - 8.0*x^5 + 1.0*x^6)

Now we use a standard numerical method for finding those roots, pretending that we don't know them already. This corresponds to $\tilde{y}$ in {numref}`Definition {number} <definition-stability-backward>`.

In [10]:
r̃ = sort(roots(p))   # type r\tilde and then press Tab

6-element Vector{Float64}:
 -2.0000000000000013
 -0.999999999999999
  0.9999999902778504
  1.0000000097221495
  2.9999999999999996
  5.999999999999992

```{index} ! Julia; @., Julia; broadcasting
```

::::{panels}
:column: col-7 left-side
:card: border-0 shadow-none
```{raw} latex
\begin{minipage}[t]{0.5\textwidth}
```
Here are the relative errors in each of the computed roots. 

```{raw} latex
\end{minipage}\hfill
```
---
:column: col-5 right-side
:card: shadow-none comment 
```{raw} latex
\begin{minipage}[t]{0.4\textwidth}\begin{mdframed}[default]\small
```
The `@.` notation at the start means to do the given operations on each element of the given vectors.
```{raw} latex
\end{mdframed}\end{minipage}
```
::::

In [11]:
println("Root errors:") 
@. abs(r-r̃) / r

Root errors:


6-element Vector{Float64}:
 -6.661338147750939e-16
 -9.992007221626409e-16
  9.722149640900568e-9
  9.722149529878266e-9
  1.4802973661668753e-16
  1.3322676295501878e-15

It seems that the forward error is acceptably close to machine epsilon for double precision in all cases except the double root at $x=1$. This is not a surprise, though, given the poor conditioning at such roots.

Let's consider the backward error. The data in the rootfinding problem are the polynomial coefficients. We can apply `fromroots` to find the coefficients of the polynomial (that is, the data) whose roots were actually computed by the numerical algorithm. This corresponds to $\tilde{x}$ in {numref}`Definition {number} <definition-stability-backward>`.

In [12]:
p̃ = fromroots(r̃)

Polynomial(35.99999999999993 - 35.999999999999915*x - 42.99999999999997*x^2 + 43.99999999999998*x^3 + 5.999999999999973*x^4 - 7.999999999999991*x^5 + 1.0*x^6)

We find that in a relative sense, these coefficients are very close to those of the original, exact polynomial:

In [13]:
c,c̃ = coeffs(p),coeffs(p̃)
println("Coefficient errors:") 
@. abs(c-c̃) / c

Coefficient errors:


7-element Vector{Float64}:
  1.973729821555834e-15
 -2.3684757858670005e-15
 -6.609699867535816e-16
  4.844609562000683e-16
  4.440892098500626e-15
 -1.1102230246251565e-15
  0.0

In summary, even though there are some computed roots relatively far from their correct values, they are nevertheless the roots of a polynomial that is very close to the original.

```{raw} html
</div>
```

```{raw} latex
%%end demo%%
```

Small backward error is the best we can hope for in a poorly conditioned problem. Without getting into the formal details, know that if an algorithm always produces small backward errors, then it is stable. But the converse is not always true: some stable algorithms may produce a large backward error.

(example-stability-notbs)=
::::{proof:example}
One stable algorithm that is not backward stable is floating-point evaluation for our old friend, $f(x)=x+1$. If $|x|<\epsilon_\text{mach}/2$, then the computed result is $\tilde{f}(x)=1$, since there are no floating-point numbers between $1$ and $1+\epsilon_\text{mach}$. Hence the only possible choice for a real number $\tilde{x}$ satisfying {eq}`backwarderror` is $\tilde{x}=0$. But then $|\tilde{x}-x|/|x|=1$, which indicates 100% backward error!
::::

## Exercises

1. The formulas

    ```{math}
    f(x)=\frac{1-\cos(x)}{\sin(x)}, \quad g(x) = \frac{2\sin^2(x/2)}{\sin(x)},
    ```
    are mathematically equivalent, but they suggest evaluation algorithms that can behave quite differently in floating point.

    **(a)** ✍ Using {eq}`conditionderiv`, find the relative condition number of $f$. (Because $f$ and $g$ are equivalent, the condition number of $g$ is the same.) Show that it approaches 1 as $x\to 0$. (Hence it should be possible to compute the function accurately near zero.)

    **(b)** ⌨ Compute $f(10^{-6})$ using a sequence of four elementary operations. Using {numref}`Table {number} <table-condition-functions>`, make a table like the one in {numref}`Demo %s <demo-stability-quadbad>` that shows the result of each elementary result and the numerical value of the condition number of that step.

    **(c)** ⌨ Repeat part (b) for $g(10^{-6})$, which has six elementary steps.

    **(d)** ✍ Based on parts (b) and (c), is the numerical value of $f(10^{-6})$ more accurate, or is $g(10^{-6})$ more accurate?
  
2. Let $f(x) = \frac{e^x-1}{x}$.
  
    **(a)** ✍ Find the condition number $\kappa_f(x)$. What is the maximum of $\kappa_f(x)$ over $-1\le x \le 1$?
  
    **(b)** ⌨  Use the "obvious" algorithm

    ``` julia
    (exp(x)-1) / x
    ```

    to compute $f(x)$ at $x=10^{-2},10^{-3},10^{-4},\ldots,10^{-11}$.  

    **(c)** ⌨ Create a second algorithm from the first 8 terms of the Maclaurin series, i.e.,

    ```{math}
    p(x) = 1 + \frac{1}{2!}x + \frac{1}{3!}x^2 + \cdots + \frac{1}{8!}x^8.
    ```

    Evaluate it at the same values of $x$ as in part (b).
  
    **(d)** ⌨  Make a table of the relative difference between the two algorithms as a function of $x$. Which algorithm is more accurate, and why?
  
3. ⌨ The function
  
    ```{math}
    x = \cosh(y) = \frac{e^y + e^{-y}}{2}
    ```

    can be inverted to yield a formula for $\operatorname{acosh}(x)$:
  
    ```{math}
    :label: acosh
    \operatorname{acosh}(x) = y = \log\bigl(x-\sqrt{x^2-1}\bigr).
    ```

    For the steps below, define $y_i=-4i$ and $x_i=\cosh(y_i)$ for $i=1,\dots,4$. Hence $y_i=\operatorname{acosh}(x_i)$.

    **(a)** Find the relative condition number of evaluating $f(x) = \operatorname{acosh}(x)$. (You can use {eq}`acosh` or look up a formula for $f'$ in a calculus book.)  Evaluate $\kappa_f$ at all the $x_i$. (You will find that the problem is well-conditioned at these inputs.)

    **(b)** Use {eq}`acosh` to approximate $f(x_i)$ for all $i$. Compute the relative accuracy of the results. Why are some of the results so inaccurate?

    **(c)** An alternative formula is

    ```{math}
    :label: acosh2
    y = -2\log\left(\sqrt{\frac{x+1}{2}} + \sqrt{\frac{x-1}{2}}\right).
    ```

    Apply {eq}`acosh2` to approximate $f(x_i)$ for all $i$, again computing the relative accuracy of the results.

4. ⌨ (Continuation of [Exercise 1.3.2](problem-algorithms-samplevar). Adapted from {cite}`highamAccuracyStability2002`.) One drawback of the formula {eq}`samplevar` for sample variance is that you must compute a sum for $\overline{x}$ before beginning another sum to find $s^2$. Some statistics textbooks quote a single-loop formula
  
    ```{math}
    \begin{split}
    s^2 &= \frac{1}{n-1} \left( u - \tfrac{1}{n}v^2 \right),\\
    u & = \sum_{i=1}^n x_i^2, \\
    v &= \sum_{i=1}^n x_i.
    \end{split}
    ```

    Try this formula for these three datasets, each of which has a variance exactly equal to 1:

    ``` julia
    x = [ 1e6, 1+1e6, 2+1e6 ]
    x = [ 1e7, 1+1e7, 2+1e7 ]
    x = [ 1e8, 1+1e8, 2+1e8 ]
    ```

    Explain the results.